In [52]:
from data import data_generation, data_picker, batch_creator, gp_kernels
from helpers import metrics
import sklearn.gaussian_process as gp 
import matplotlib.pyplot as plt
import numpy as np
import scipy
plt.style.use('ggplot')

%matplotlib inline

In [80]:
extrapo = False

In [81]:
if extrapo:
    x = np.load('/Users/omernivron/Downloads/GPT_data_goldstandard/x_extra.npy')
    y = np.load('/Users/omernivron/Downloads/GPT_data_goldstandard/y_extra.npy')
else:
    x = np.load('/Users/omernivron/Downloads/GPT_data_goldstandard/x_interpol.npy')
    y = np.load('/Users/omernivron/Downloads/GPT_data_goldstandard/y_interpol.npy')

In [92]:
def predict_golden(t, x, x_star):
    n = x.shape[0]
#     print(n)
    xx = np.concatenate((x, x_star), axis = 0)
    d = np.zeros((n, n))
    np.fill_diagonal(d, 0.00001)
    K_inv = np.linalg.inv(gp_kernels.rbf_kernel(x) + d) 
#     print('k_inv: ', K_inv)
    k_t = (gp_kernels.rbf_kernel(xx.reshape(-1, 1))[:-1, -1]).transpose() 
#     print('k_t: ', k_t)
    μ = np.dot(np.dot(k_t, K_inv), t)
    σ_sq = 1 - np.dot(np.dot(k_t, K_inv), k_t.transpose())
    return μ, σ_sq

In [93]:
# GP independent sequence learning  
online = False; mse_metric = 0; r_sq_metric = 0; kuee_metric = 0
μ = []; σ = []; k= []; ρ= [];
μ_g = []; σ_g = [];
m = int(x.shape[0] / 10)
# x[:, :40] = (x[:, :40] - np.mean(x[:, :40])) / np.std(x[:, :40])
# x[:, 40] = (x[:, 40] - np.mean(x[:, :40])) / np.std(x[:, :40])
y_mean = np.mean(y[:m, :40])
y_te = y[:m, 40]
for j in range(0, m):
    λ=np.exp(-1); ν = 1; σ1 = 0.0001;
    kernel = ν**2 * gp.kernels.RBF(length_scale=λ)
    model = gp.GaussianProcessRegressor(kernel=kernel, n_restarts_optimizer = 3, normalize_y=True)
    x_tr =  x[j, :40].reshape(-1, 1); y_tr = y[j, :40].reshape(-1, 1)

    model.fit(x_tr, y_tr)
    μ_te, σ_te = model.predict(x[j, 40].reshape(-1, 1), return_std=True)
    μ_gold, σ_sq_gold = predict_golden(y_tr, x_tr, x[j, 40].reshape(-1, 1))
    μ.append(μ_te); σ.append(σ_te)
    μ_g.append(μ_gold); σ_g.append(σ_sq_gold)
    k.append(model.kernel_.get_params()['k2'])
    ρ.append(model.kernel_.get_params()['k1'])

    kuee_metric += metrics.KUEE(y_te[j], μ_te, σ_te)
    
mse_metric = metrics.mse(y_te, μ)
mse_metric2 = metrics.mse(y_te, μ_g)


r_sq_metric = metrics.r_squared(y_te, μ, y_mean)
mse_metric *= (1 / m)
mse_metric2 *= (1 / m)
kuee_metric *= (1 / m)

/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([ 0.07358804, -0.0911835 ]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 101, 'nit': 10, 'warnflag': 2}
  ConvergenceWarning)
/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([ 11.4661642, -80.0498862]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 51, 'nit': 3, 'warnflag': 2}
  ConvergenceWarning)


k_inv:  [[81401.21304832  -992.79770211   210.40979968 ...  3264.53092032
  -8507.970789     628.64289034]
 [ -992.79770161 87836.33764468  1592.53780101 ...   310.18483802
   -291.23739002  1625.95356577]
 [  210.40979949  1592.53780083 86601.15759672 ... -1671.16077323
   2592.25012554  -890.73662996]
 ...
 [ 3264.53092054   310.18483791 -1671.16077316 ... 25663.36645207
   -979.52190976   380.74651189]
 [-8507.97078879  -291.23738996  2592.25012548 ...  -979.52190968
  74891.31892012  -555.19347999]
 [  628.64288992  1625.95356502  -890.73662987 ...   380.74651184
   -555.19347988 68678.72105076]]
k_t:  [1.70192469e-15 7.52868068e-20 1.64573194e-17 1.13135164e-13
 2.16995946e-11 1.13745382e-18 6.87868009e-20 2.13849663e-13
 1.60410103e-20 3.93126693e-18 1.78324602e-12 1.46006840e-19
 1.57022555e-19 5.21683193e-22 2.22688324e-14 4.84055695e-17
 1.08700762e-17 1.00490954e-15 1.66137043e-15 2.27266490e-12
 3.15302920e-16 9.73618395e-18 6.57492871e-21 1.60844419e-19
 2.16722621e-17 2.65

/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([0.38525391, 2.3142395 ]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 78, 'nit': 15, 'warnflag': 2}
  ConvergenceWarning)
/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([ 11.65510344, -83.37971105]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 27, 'nit': 1, 'warnflag': 2}
  ConvergenceWarning)


k_inv:  [[ 7.97080767e+04 -1.03528188e+04 -3.87703433e+02 ... -5.91838015e+03
  -3.24648234e+02  1.44602326e+02]
 [-1.03528188e+04  8.87781777e+04  4.22140686e+02 ... -1.05104950e+04
   2.04992887e+03 -7.20674874e+02]
 [-3.87703433e+02  4.22140686e+02  6.76513395e+04 ...  5.10453247e+02
  -4.72654975e+02  4.88776931e+02]
 ...
 [-5.91838015e+03 -1.05104950e+04  5.10453247e+02 ...  8.86971219e+04
   1.93104266e+03 -6.62627357e+02]
 [-3.24648234e+02  2.04992887e+03 -4.72654975e+02 ...  1.93104265e+03
   7.88263851e+04  2.78644890e+01]
 [ 1.44602326e+02 -7.20674874e+02  4.88776932e+02 ... -6.62627359e+02
   2.78644874e+01  8.48541505e+04]]
k_t:  [9.96165629e-27 1.99038188e-27 7.11790559e-42 5.83828922e-26
 9.34956808e-26 7.17900166e-27 5.73900707e-30 1.52551323e-29
 1.72014696e-42 1.47183251e-27 1.85577984e-25 4.87932381e-37
 2.31532411e-27 9.29053469e-34 9.01499654e-32 1.06388086e-25
 6.89650183e-29 9.76230061e-26 1.17951611e-27 3.59545329e-29
 5.71217660e-39 2.70464365e-41 1.77778339e-36

/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([  5.9110042 , -59.94594631]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 77, 'nit': 8, 'warnflag': 2}
  ConvergenceWarning)


...

/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([ 12.04802293, -86.81743884]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 42, 'nit': 2, 'warnflag': 2}
  ConvergenceWarning)
/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([-0.00219727,  0.0006876 ]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 120, 'nit': 14, 'warnflag': 2}
  ConvergenceWarning)
/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([   9.        , -109.10095215]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 21, 'nit': 0, 'warnflag': 2}
  ConvergenceWarning)


k_inv:  [[ 78216.42167932 -12986.89192769 -20252.49730891 ...   1648.67379564
   -1578.51714985   1419.36403499]
 [-12986.89192792  87102.27595512  -8303.73277639 ...   3618.4856961
   -1521.88397527  -4143.07217145]
 [-20252.49730923  -8303.73277645  76754.54720404 ...   -961.59446886
    -337.33006412   2964.9353424 ]
 ...
 [  1648.67379527   3618.48569571   -961.59446954 ...  81967.32043619
   -3002.62755581  -2723.64282356]
 [ -1578.51714924  -1521.88397514   -337.33006427 ...  -3002.62755483
   85576.38830779   1495.34573149]
 [  1419.3640354   -4143.07217104   2964.93534183 ...  -2723.6428258
    1495.34572887  90422.71818654]]
k_t:  [3.91572799e-39 7.58358874e-38 4.67725681e-40 1.13406035e-41
 7.42733109e-32 1.38839587e-36 4.54029488e-42 7.25975105e-47
 1.34707703e-36 2.64324294e-34 5.94526439e-31 1.44945223e-29
 4.02603749e-38 2.62630444e-32 9.95008653e-35 3.58797822e-29
 1.47854507e-32 2.59648119e-31 1.98822411e-43 9.85300802e-37
 4.57779020e-45 2.98319230e-31 3.77341914e-37 1

k_inv:  [[ 47974.1355727     675.46135851   -885.38691041 ...   2265.67431365
    1895.93541454   4510.79842722]
 [   675.46135824  87025.26488643   1679.56702932 ...  -5057.57125057
  -13769.77138765   -635.82938566]
 [  -885.38691051   1679.56702934  74909.01698133 ...   5317.83427473
    4382.78722855  -7745.5764689 ]
 ...
 [  2265.67431383  -5057.57125047   5317.83427411 ...  79248.16629658
   -9688.19836114    586.19538832]
 [  1895.93541442 -13769.77138773   4382.78722695 ...  -9688.19836207
   83731.71572072   -900.73190236]
 [  4510.79842787   -635.82938557  -7745.57646996 ...    586.19538764
    -900.73190112  86787.62937069]]
k_t:  [5.21771730e-31 1.78352774e-23 2.01599510e-28 2.05161667e-21
 1.59013775e-25 1.35187722e-21 6.43566782e-31 6.60071945e-22
 7.73115899e-30 8.44088244e-19 2.26081681e-18 5.49089939e-29
 3.50019122e-23 1.01497940e-29 3.35930428e-30 1.48443523e-22
 1.13128240e-26 4.39306877e-20 2.74022606e-22 4.06380338e-21
 1.43976512e-18 1.53678533e-26 4.13842797e-20

/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([-0.00222301, -0.00910342]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 95, 'nit': 13, 'warnflag': 2}
  ConvergenceWarning)
/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([  9.38894516, -12.17355054]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 95, 'nit': 13, 'warnflag': 2}
  ConvergenceWarning)
/Users/omernivron/opt/anaconda3/lib/python3.7/site-packages/sklearn/gaussian_process/gpr.py:469: ConvergenceWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([  4.57617188, -82.2838974 ]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 39, 'nit': 2, 'warnflag': 2}
  ConvergenceWarning)


k_inv:  [[ 84537.68874713   -692.88011477 -14987.03603242 ...   1282.66150376
   -1775.37149681    109.59723178]
 [  -692.88011479  80534.8288487     710.5157811  ...    850.72316784
    -714.20854023   -812.22860321]
 [-14987.03603297    710.51578127  84065.15338735 ...   1850.1525546
   -1166.61733988   -534.55711983]
 ...
 [  1282.66150389    850.72316789   1850.15255458 ...  68527.66257065
  -12127.41112599   -387.82112271]
 [ -1775.37149767   -714.20854044  -1166.61734003 ... -12127.41112676
   79619.43483352    410.99264864]
 [   109.59723203   -812.22860329   -534.55711948 ...   -387.82112259
     410.99264835  76314.8318639 ]]
k_t:  [2.97813696e-23 3.91120361e-19 7.23721183e-23 1.92705799e-21
 1.14410966e-19 1.28788399e-26 5.34979469e-17 7.67318710e-25
 1.43031681e-17 6.52768795e-22 3.09468347e-25 7.60405207e-31
 1.58359176e-28 2.27968068e-24 1.28608470e-26 3.69591986e-18
 4.06689494e-19 1.10701114e-22 2.49070132e-17 5.18903091e-29
 6.29888986e-28 5.25807592e-25 8.82386871e-20 

In [97]:
mse_metric

121763.01545473872

In [98]:
mse_metric2

115084.50628565662

In [91]:
ρ

[3.49**2,
 1.24**2,
 2.47**2,
 12**2,
 1**2,
 1**2,
 5.21**2,
 1**2,
 5.7**2,
 5.44**2,
 6.89**2,
 1**2,
 3.54**2,
 51.4**2,
 1**2,
 2.8**2,
 1.8**2,
 4.22**2,
 3.96**2,
 1**2,
 2.5**2,
 5.96**2,
 2.88**2,
 305**2,
 12.8**2,
 1**2,
 1.8**2,
 1**2,
 1**2,
 1**2,
 1**2,
 5.14**2,
 2.29**2,
 2.48**2,
 1**2,
 1**2,
 1**2,
 1**2,
 1.88**2,
 316**2,
 1**2,
 2.09**2,
 1**2,
 1**2,
 1.94**2,
 1**2,
 1**2,
 1**2,
 6.57**2,
 8.53**2,
 1.52**2,
 1**2,
 2.94**2,
 3.46**2,
 1.81**2,
 1**2,
 3.83**2,
 3.52**2,
 2.36**2,
 3.28**2,
 7.42**2,
 4.4**2,
 12.2**2,
 9.42**2,
 2.08**2,
 4.16**2,
 1**2,
 1**2,
 7.46**2,
 1**2,
 2.46**2,
 7.67**2,
 1**2,
 3.82**2,
 3.15**2,
 2.96**2,
 5.18**2,
 4.23**2,
 1**2,
 2.71**2,
 2.29**2,
 8.13**2,
 1**2,
 5.4**2,
 1**2,
 3.76**2,
 2.88**2,
 1**2,
 2.24**2,
 1**2,
 1**2,
 1**2,
 5.72**2,
 9.94**2,
 3.31**2,
 2.97**2,
 3.47**2,
 6.34**2,
 1**2,
 1**2,
 3.28**2,
 1**2,
 6.24**2,
 6.72**2,
 5.31**2,
 1**2,
 4.3**2,
 10.2**2,
 6.99**2,
 1**2,
 2.9**2,
 5.26**2,
 1.49**2,


In [70]:
x[j, 40]

8.50232783508508

In [96]:
μ_g

[array([1.55169193e-06]),
 array([0.00132879]),
 array([1.36380352e-06]),
 array([-2.60959713e-21]),
 array([-1.1535978]),
 array([6.6784859e-31]),
 array([2.638992e-23]),
 array([-9.39594912e-12]),
 array([2.59688618e-10]),
 array([8.28382485]),
 array([0.00361999]),
 array([-0.00613097]),
 array([7.33950835e-22]),
 array([2.32240968e-07]),
 array([-1.28082268e-13]),
 array([9.67905571e-34]),
 array([3.54333633e-06]),
 array([-4.01288996e-12]),
 array([3.28562217e-14]),
 array([3.3489331e-11]),
 array([-1.88010925e-22]),
 array([8.22396637e-22]),
 array([4.75716443e-12]),
 array([-0.64037276]),
 array([1.14776748e-28]),
 array([7.97224915e-05]),
 array([0.05578122]),
 array([-8.80477734e-25]),
 array([-4.45035029e-08]),
 array([-1.04353765e-08]),
 array([-0.55150716]),
 array([0.00271786]),
 array([5.33757623e-14]),
 array([-1.40360082e-19]),
 array([0.01977647]),
 array([-1.49703187e-18]),
 array([3.52950283e-09]),
 array([-7.02069232e-11]),
 array([-6.75078565e-08]),
 array([6.13350

In [60]:
y

array([[  2.71903994,   1.38880796,  -4.80930659, ...,  -3.8118663 ,
         -2.25327172,  -0.35500322],
       [ -8.5910372 ,  -7.67848009,  -0.3592382 , ...,  -2.92383064,
         -4.87708551,   2.86637182],
       [ -0.18465114, -15.53458292, -10.47361226, ...,   3.84607437,
          2.36463512,   3.8772359 ],
       ...,
       [ -1.87867593,   0.73578189,  -4.95419572, ...,   0.8466218 ,
          1.91912307,   4.56620165],
       [ -5.84201552,   1.10960528,   6.74974129, ...,  -0.7609906 ,
          4.25462313,   3.78221031],
       [  0.92078039,  -7.07567869,  -5.58918997, ...,   9.00232566,
          9.92176591,   6.81730146]])

In [59]:
k

[RBF(length_scale=1e-05),
 RBF(length_scale=0.342),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.281),
 RBF(length_scale=0.306),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.301),
 RBF(length_scale=0.188),
 RBF(length_scale=0.329),
 RBF(length_scale=1e-05),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.00101),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.196),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.155),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.25),
 RBF(length_scale=0.289),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.0158),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.288),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.262),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.311),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.152),
 RBF(length_scale=1e-05),
 RBF(length_scale=0.327),
 RBF(length_scale=0.0976),
 RBF(length_scale=0.229),
 RBF(length_scale=0.174),
 RBF(length_scale=0.277),
 RBF(length_scale=0.337),
 RBF(length_scale=1e-05),
 RBF(length_scale=1e-05),
 RBF(leng

In [43]:
mse_metric

2006.872985500104

In [99]:
kuee_metric

0.894

In [44]:
r_sq_metric

-2001.444536640471

In [45]:
ρ

[0.827**2 * RBF(length_scale=0.36),
 1.14**2 * RBF(length_scale=0.36),
 0.824**2 * RBF(length_scale=0.329),
 1.2**2 * RBF(length_scale=0.353),
 1.29**2 * RBF(length_scale=0.367),
 0.854**2 * RBF(length_scale=0.341),
 0.879**2 * RBF(length_scale=0.349),
 1.51**2 * RBF(length_scale=0.361),
 0.694**2 * RBF(length_scale=0.33),
 1.07**2 * RBF(length_scale=0.38),
 0.826**2 * RBF(length_scale=0.326),
 0.834**2 * RBF(length_scale=0.355),
 0.842**2 * RBF(length_scale=0.333),
 0.929**2 * RBF(length_scale=0.351),
 0.943**2 * RBF(length_scale=0.395),
 1.67**2 * RBF(length_scale=0.369),
 0.939**2 * RBF(length_scale=0.339),
 1.4**2 * RBF(length_scale=0.348),
 0.769**2 * RBF(length_scale=0.34),
 0.739**2 * RBF(length_scale=0.316),
 1**2 * RBF(length_scale=0.378),
 1.26**2 * RBF(length_scale=0.39),
 0.833**2 * RBF(length_scale=0.334),
 1.09**2 * RBF(length_scale=0.377),
 1.47**2 * RBF(length_scale=0.395),
 1.11**2 * RBF(length_scale=0.369),
 0.869**2 * RBF(length_scale=0.355),
 0.794**2 * RBF(length_s

In [46]:
mse_metric = metrics.mse(y_te, μ_g)

In [48]:
mse_metric / m

2006.872985500104

In [30]:
mse_metric /m 

2499.723037936542

In [12]:
kuee_metric

0.925

In [5]:

#     fig, axes = plt.subplots(1, 1, figsize=(8, 6))
#     axes.set_ylim(-1, 1)
#     axes.scatter(xx_tr, yy_tr, c = 'black')
#         axes.scatter(xx_te, yy_te, c='purple', label = 'true y')
#         axes.scatter(xx_te, μ_te, c='blue', label = 'predicted y')
#         axes.errorbar(xx_te, μ_te, yerr = [ 2 * σ_te], c ='navy')
#         axes.legend()

#         plt.show()
#         plt.close()